In [3]:
from IPython.display import display
from IPython.display import HTML
import IPython.core.display as di # Example: di.display_html('<h3>%s:</h3>' % str, raw=True)

# This line will hide code by default when the notebook is exported as HTML
# di.display_html('<script>jQuery(function() {if (jQuery("body.notebook_app").length == 0) { jQuery(".input_area").toggle(); jQuery(".prompt").toggle();}});</script>', raw=True)

display(HTML("<style>.container { width:100% !important; }</style>"))

In [4]:
import hail as hl
hl.init(tmp_dir='/net/scratch/people/plggosborcz')

Running on Apache Spark version 2.4.5
SparkUI available at http://p0905.prometheus:4040
Welcome to
     __  __     <>__
    / /_/ /__  __/ /
   / __  / _ `/ / /
  /_/ /_/\_,_/_/_/   version 0.2.62-84fa81b9ea3d
LOGGING: writing to /net/archive/groups/plggneuromol/GTS-analysis/imdik-zekanowski-gts/hail-20210705-1828-0.2.62-84fa81b9ea3d.log


In [5]:
display(HTML("<style>.container { width:100% !important; }</style>"))

In [6]:
from hail.plot import show
from pprint import pprint
from bokeh.layouts import gridplot
hl.plot.output_notebook()

import numpy as np
import pandas as pd
from functools import reduce
from itertools import chain
import statistics as stat

import bokeh.palettes

Loading BokehJS ...

In [7]:
from bokeh.plotting import figure, show, output_notebook
output_notebook()

Loading BokehJS ...

## Load SKAT functions

In [8]:
def run_skat_log(mtx, gene_list, pcs):
    
    mtx = mtx.filter_rows(hl.any(lambda x: hl.literal(gene_list).contains(x), mtx.nearest_genes_20kb))
    mtx = mtx.filter_rows(hl.agg.any(mtx.GT.is_non_ref()))
    mtx = mtx.explode_rows(mtx.nearest_genes_20kb)
    mtx = mtx.filter_rows(hl.literal(gene_list).contains(mtx.nearest_genes_20kb))
    
    
    scores = [mtx.scores[x] for x in list(range(pcs))]
                          
    
    skat_table = hl.skat(
                         key_expr=mtx.nearest_genes_20kb,
                         weight_expr=mtx.cadd,
                         y=mtx.category,
                         x=mtx.GT.n_alt_alleles(),
                         covariates=[1] + scores,
                         max_size = 2500,
                         logistic = True)
    
    genes_result = skat_table.filter(skat_table.p_value < 0.05/len(gene_list)).id.collect() 

    
    skat_table.order_by('p_value').show(20)
    #skat_table.filter(skat_table.p_value < 0.002).show(20)

    qq_plot = hl.plot.qq(skat_table.p_value)
    qq_plot.xaxis.axis_label_text_font_size = "15pt"
    qq_plot.xaxis.major_label_text_font_size = "15pt"
    qq_plot.yaxis.axis_label_text_font_size = "15pt"
    qq_plot.yaxis.major_label_text_font_size = "15pt"
    
    show(qq_plot)
    
    
    return(skat_table, genes_result, qq_plot)

In [23]:
def test_model(geneset_name):  
    for c_idx, c in enumerate(cadds):

        test_asignment = np.zeros((len(top_genes), 145)) 
        mt_skat_log = hl.read_matrix_table('/net/archive/groups/plggneuromol/GTS-analysis/data/mt_for_skat_'+str(c)+'.mt')
        mt_test_skat_log = hl.read_matrix_table('/net/archive/groups/plggneuromol/GTS-analysis/data/mt_test_'+str(c)+'.mt')
      
        for rows, n in enumerate(top_genes):

            mt_skat_log_gene = mt_skat_log.filter_rows(mt_skat_log.nearest_genes_20kb.contains(n)) # to ma gnomadów i heavy tics
        
            mt_test_skat_log_gene = mt_test_skat_log.filter_rows(mt_test_skat_log.nearest_genes_20kb.contains(n)) # to ma rodziny

            mt_skat_log_gene = mt_skat_log_gene.annotate_cols(non_refs = hl.agg.count_where(mt_skat_log_gene.GT.is_non_ref())) #count variants per sample of gnomads and heavy tics  
            non_refs = mt_skat_log_gene.non_refs.collect()
                                                
            mt_test_skat_log_gene = mt_test_skat_log_gene.annotate_cols(non_refs = hl.agg.count_where(mt_test_skat_log_gene.GT.is_non_ref())) #count variants per sample, prepare also test matrix
            non_refs_test = mt_test_skat_log_gene.non_refs.collect()

            variants_controls = np.mean(np.array(non_refs)[np.invert(categories)])
                
            test_asignment[rows] = (non_refs_test - variants_controls)
            
            print(test_asignment.shape)
                
        for s in sets:
        
            test_asignment_subset = test_asignment[range(5-s,5), :]
            
            print(test_asignment_subset.shape)
                
            test_asignment_subset = np.sum(test_asignment_subset, axis = 0)
                
            false_pos = []
            true_pos = []
            
            for x in np.linspace(-100,100,10000):
            
                false_pos.append(np.sum((test_asignment_subset > x)[np.invert(categories_test)])/56)
                true_pos.append(np.sum((test_asignment_subset > x)[categories_test])/89)
            
            print(np.trapz(false_pos, true_pos))
        
            np.save('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-false_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name, false_pos)
            np.save('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-true_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name, true_pos)

    
    false_pos = []
    true_pos = []

    for s in sets:
        for c in cadds:
            a = np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-false_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name+'.npy')
            b = np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-true_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name+'.npy')
            
            if (a[0] == 1) & (a[9999] == 0) & (b[0] == 1) & (b[9999] == 0):
                false_pos.append(a)
                true_pos.append(b)

    aucs = []
    for i in range(0,14):
        aucs.append(np.trapz(true_pos[i], false_pos[i]))

    aucs = np.array(aucs)
    print(aucs)

    test1 = np.array(([0,1,2,4,5], [0,2,2,3,5]))
    test2 = np.array(([1,1,1,1,1], [2,2,2,2,2]))

    y = np.linspace(0,1,10)
    x = np.linspace(0,1,10)

    false_pos_ori = []
    true_pos_ori = []

    for s in sets:
        for c in cadds:
            false_pos_ori.append(np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-false_pos'+str(s)+'cadd'+str(c)+'.npy'))
            true_pos_ori.append(np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-true_pos'+str(s)+'cadd'+str(c)+'.npy'))

    p4 = figure(plot_width=800, plot_height=800)
    p4.line(x, y, line_width=4, line_color='lightgrey')


    for i in range(0,14):
        p4.line(false_pos[i], true_pos[i], line_width=1, alpha=0.25)
    
    p4.line(false_pos_ori[13], true_pos_ori[13], line_width=4, line_color='orange')

    p4.xaxis.axis_label = 'false positives'
    p4.yaxis.axis_label = 'true positives'


    p4.xaxis.axis_label_text_font_size = "15pt"
    p4.xaxis.major_label_text_font_size = "15pt"
    p4.yaxis.axis_label_text_font_size = "15pt"
    p4.yaxis.major_label_text_font_size = "15pt"
    p4.title.text = geneset_name
    p4.title.text_font_size = "20px"

    # show the results
    show(p4)

In [13]:
sets = [2,3,4,5]
cadds = [5,10,15,20]

## Run SKAT on all genes

In [9]:
allgenes= np.load('/net/archive/groups/plggneuromol/GTS-analysis/analysis/numpy/genes_background.npy')

In [10]:
allgenes.shape

(18122,)

In [27]:
mt = hl.read_matrix_table('/net/archive/groups/plggneuromol/GTS-analysis/data/mt-for-model-expanded-may.mt') #this goes into each model

In [28]:
mt_for_skat = hl.read_matrix_table('/net/archive/groups/plggneuromol/GTS-analysis/data/mt-for-skat-may.mt')
mt_test = hl.read_matrix_table('/net/archive/groups/plggneuromol/GTS-analysis/data/mt-test-may.mt')
categories = mt_for_skat.category.collect()
categories_test = mt_test.category.collect()

In [ ]:
skat_table, genes_result, qq_plot = run_skat_log(mt, list(allgenes), 9)

2021-07-05 18:06:51 Hail: INFO: Ordering unsorted dataset with network shuffle
2021-07-05 18:15:04 Hail: INFO: Ordering unsorted dataset with network shuffle


+------------+-------+----------+----------+-------+
| id         |  size |   q_stat |  p_value | fault |
+------------+-------+----------+----------+-------+
| str        | int32 |  float64 |  float64 | int32 |
+------------+-------+----------+----------+-------+
| "PCNT"     |   497 | 2.74e+03 | 2.32e-07 |     0 |
| "CNN2"     |   262 | 2.89e+03 | 4.84e-07 |     0 |
| "TMEM259"  |   325 | 3.81e+03 | 5.58e-07 |     0 |
| "FRG2"     |   337 | 3.62e+03 | 7.05e-07 |     0 |
| "DUX4"     |    15 | 1.61e+03 | 1.19e-06 |     0 |
| "SERPINA1" |   342 | 1.78e+03 | 1.28e-06 |     0 |
| "OR2A2"    |   103 | 1.62e+03 | 1.87e-06 |     0 |
| "CHEK2"    |   144 | 1.36e+03 | 2.02e-06 |     0 |
| "NEK7"     |   410 | 3.32e+03 | 2.04e-06 |     0 |
| "SERPINA2" |   318 | 1.73e+03 | 2.24e-06 |     0 |
| "ABCA7"    |   233 | 2.70e+03 | 2.49e-06 |     0 |
| "PPP1R3A"  |   286 | 1.98e+03 | 2.86e-06 |     0 |
| "MAP7D3"   |    72 | 2.56e+03 | 2.93e-06 |     0 |
| "PPP3CA"   |   772 | 4.65e+03 | 4.33e-06 |     0 |
| "OR2A14"   |   127 | 1.86e+03 | 4.82e-06 |     0 |
| "AFTPH"    |   153 | 2.47e+03 | 6.59e-06 |     0 |
| "FRG2C"    |  1011 | 1.05e+04 | 6.72e-06 |     0 |
| "FHL1"     |    80 | 2.22e+03 | 7.67e-06 |     0 |
| "PRDX5"    |    72 | 1.56e+03 | 8.12e-06 |     0 |
| "OR2A12"   |    99 | 1.36e+03 | 8.63e-06 |     0 |
+------------+-------+----------+----------+-------+
showing top 20 rows

In [ ]:
skat_table.checkpoint('/net/archive/groups/plggneuromol/GTS-analysis/data/skat-all.mt')

In [11]:
#assign top genes manually
top_genes = ['PCNT', 'CNN2', 'TMEM259', 'FRG2', 'DUX4']

In [15]:
test_model('allgenes')

(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5400280898876405
(3, 145)
-0.562800963081862
(4, 145)
-0.5676163723916533
(5, 145)
-0.5565810593900482
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.49939807383627605
(3, 145)
-0.5114365971107544
(4, 145)
-0.5298956661316212
(5, 145)
-0.5359149277688604
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5416332263242376
(3, 145)
-0.4826444622792937
(4, 145)
-0.4843499197431782
(5, 145)
-0.4910714285714286
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5208667736757624
(3, 145)
-0.47943418940609955
(4, 145)
-0.4965890850722311
(5, 145)
-0.507223113964687


IndexError: list index out of range

In [17]:
geneset_name='allgenes'

In [18]:
false_pos = []
true_pos = []

for s in sets:
    for c in cadds:
        a = np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-false_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name+'.npy')
        b = np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-true_pos'+str(s)+'cadd'+str(c)+'gene'+geneset_name+'.npy')
           
        if (a[0] == 1) & (a[9999] == 0) & (b[0] == 1) & (b[9999] == 0):
            false_pos.append(a)
            true_pos.append(b)

In [19]:
len(true_pos)

14

In [22]:
aucs = []

for i in range(0,14):
    aucs.append(np.trapz(true_pos[i], false_pos[i]))

aucs = np.array(aucs)
print(aucs)

test1 = np.array(([0,1,2,4,5], [0,2,2,3,5]))
test2 = np.array(([1,1,1,1,1], [2,2,2,2,2]))

y = np.linspace(0,1,10)
x = np.linspace(0,1,10)

false_pos_ori = []
true_pos_ori = []

for s in sets:
    for c in cadds:
        false_pos_ori.append(np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-false_pos'+str(s)+'cadd'+str(c)+'.npy'))
        true_pos_ori.append(np.load('/net/archive/groups/plggneuromol/GTS-analysis/data/numpy/may-true_pos'+str(s)+'cadd'+str(c)+'.npy'))

p4 = figure(plot_width=800, plot_height=800)
p4.line(x, y, line_width=4, line_color='lightgrey')


for i in range(0,14):
    p4.line(false_pos[i], true_pos[i], line_width=1, alpha=0.25)

p4.line(false_pos_ori[13], true_pos_ori[13], line_width=4, line_color='orange')

p4.xaxis.axis_label = 'false positives'
p4.yaxis.axis_label = 'true positives'


p4.xaxis.axis_label_text_font_size = "15pt"
p4.xaxis.major_label_text_font_size = "15pt"
p4.yaxis.axis_label_text_font_size = "15pt"
p4.yaxis.major_label_text_font_size = "15pt"
p4.title.text = geneset_name
p4.title.text_font_size = "20px"

# show the results
show(p4)

[-0.45997191 -0.50060193 -0.45836677 -0.47913323 -0.43719904 -0.4885634
 -0.51735554 -0.52056581 -0.47010433 -0.51565008 -0.50341091 -0.46408507
 -0.50892857 -0.49277689]


## run model on other gene lists

- brain enriched
- other gene lists

In [24]:
genes_neuro = list(set([line.rstrip('\n') for line in open('/net/archive/groups/plggneuromol/GTS-analysis/analysis/gts_gene_lists/brain_enriched.txt')]))

In [25]:
len(genes_neuro)

488

In [29]:
skat, genes_result, qq_plot = run_skat_log(mt, genes_neuro, 9)

2021-07-05 19:01:25 Hail: INFO: Ordering unsorted dataset with network shuffle
2021-07-05 19:03:03 Hail: INFO: Ordering unsorted dataset with network shuffle


+------------+-------+----------+----------+-------+
| id         |  size |   q_stat |  p_value | fault |
+------------+-------+----------+----------+-------+
| str        | int32 |  float64 |  float64 | int32 |
+------------+-------+----------+----------+-------+
| "KCNK4"    |    81 | 1.37e+03 | 2.54e-05 |     0 |
| "S100B"    |   103 | 8.07e+02 | 6.18e-05 |     0 |
| "GABRA2"   |   375 | 2.13e+03 | 1.19e-04 |     0 |
| "GRM1"     |   575 | 2.35e+03 | 5.58e-04 |     0 |
| "ENO2"     |    73 | 1.17e+03 | 5.81e-04 |     0 |
| "RTP5"     |   192 | 8.70e+02 | 7.26e-04 |     0 |
| "NRXN2"    |   272 | 1.85e+03 | 8.14e-04 |     0 |
| "STXBP1"   |   165 | 9.54e+02 | 1.03e-03 |     0 |
| "VAX1"     |    66 | 3.62e+02 | 1.12e-03 |     0 |
| "SLC26A5"  |   186 | 8.63e+02 | 1.15e-03 |     0 |
| "SLC5A7"   |   126 | 7.84e+02 | 1.39e-03 |     0 |
| "CSMD3"    |  2152 | 7.87e+03 | 1.41e-03 |     0 |
| "DRP2"     |    92 | 1.51e+03 | 1.56e-03 |     0 |
| "TFAP2D"   |   143 | 9.04e+02 | 1.72e-03 |     0 |
| "PLP1"     |    41 | 4.17e+02 | 1.87e-03 |     0 |
| "SNX32"    |   156 | 1.39e+03 | 2.01e-03 |     0 |
| "CHRM5"    |   283 | 9.14e+02 | 2.09e-03 |     0 |
| "MGAT5B"   |   433 | 2.01e+03 | 2.10e-03 |     0 |
| "PTPRR"    |   729 | 2.11e+03 | 2.27e-03 |     0 |
| "IL1RAPL1" |  1326 | 6.93e+03 | 3.09e-03 |     0 |
+------------+-------+----------+----------+-------+
showing top 20 rows

2021-07-05 19:04:43 Hail: INFO: Ordering unsorted dataset with network shuffle
2021-07-05 19:04:48 Hail: INFO: Coerced sorted dataset
2021-07-05 19:04:48 Hail: INFO: Coerced dataset with out-of-order partitions.


#top genes:

"KCNK4"	81	1.37e+03	2.54e-05	0
"S100B"	103	8.07e+02	6.18e-05	0
"GABRA2"	375	2.13e+03	1.19e-04	0
"GRM1"	575	2.35e+03	5.58e-04	0
"ENO2"	73	1.17e+03	5.81e-04	0

In [30]:
top_genes = skat.order_by('p_value').id.take(5)
test_model('neuro')

2021-07-05 19:06:26 Hail: INFO: Ordering unsorted dataset with network shuffle


(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5111356340288925
(3, 145)
-0.5381219903691814
(4, 145)
-0.5292937399678972
(5, 145)
-0.5510634028892456
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5086276083467095
(3, 145)
-0.5085272873194222
(4, 145)
-0.5022070626003211
(5, 145)
-0.569723113964687
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.5189606741573034
(3, 145)
-0.5479534510433386
(4, 145)
-0.5507624398073837
(5, 145)
-0.590790529695024
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(5, 145)
(2, 145)
-0.4849518459069021
(3, 145)
-0.4849518459069021
(4, 145)
-0.4849518459069021
(5, 145)
-0.5463483146067416
[-0.48886437 -0.49137239 -0.48103933 -0.51504815 -0.46187801 -0.49147271
 -0.45204655 -0.51504815 -0.47070626 -0.49779294 -0.44923756 -0.51504815
 -0.4489366  -0.43027689]
